<a href="https://colab.research.google.com/github/patal-dev/april/blob/main/FnV_Experiment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [24]:
%matplotlib inline

import logging
logging.getLogger('googleapiclient.discovery_cache').setLevel(logging.ERROR)

# Code to read csv file into Colaboratory:
!pip install -U -q PyDrive
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
# Authenticate and create the PyDrive client.
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
link = 'https://drive.google.com/open?id=1XcFFQS1ZoUOPs9vSJcA_o-Z1rvxi1Kod'
fluff, id = link.split('=')

downloaded = drive.CreateFile({'id':id}) 
downloaded.GetContentFile('wiki.mat')

## Data



*   dob: date of birth (Matlab serial date number)
*photo_taken: year when the photo was taken
*full_path: path to file
*gender: 0 for female and 1 for male, NaN if unknown
*name: name of the celebrity
*face_location: location of the face. 
*face_score: detector score (the higher the better). Inf implies that no face was found in the image and the face_location then just returns the entire image
*second_face_score: detector score of the face with the second highest score. This is useful to ignore images with more than one face. second_face_score is NaN if no second face was detected.
*celeb_names (IMDB only): list of all celebrity names
*celeb_id (IMDB only): index of celebrity name



In [57]:
import scipy.io
import numpy as np

mat = scipy.io.loadmat('wiki.mat')
fields = ('dob', 'photo_taken', 'full_path', 'gender', 'name', 
          'face_location', 'face_score', 'second_face_score')

l = 62328
data = np.empty((0, l))
# data = np.array([])
for i, field in enumerate(fields):
  if field == 'face_location':
    data = np.append(data, [np.empty(l)], axis=0)
    continue
  values = np.hstack(mat['wiki'][0][0][i].flatten())
  if len(values) < l:
    print(field, len(values))
    remainder = np.empty(l - len(values))
    values = np.concatenate((values, remainder))
  data = np.append(data, [values], axis=0)

print(data)

name 62204
[['723671.0' '703186.0' '711677.0' ... '720620.0' '723893.0' '713846.0']
 ['2009.0' '1964.0' '2008.0' ... '2013.0' '2011.0' '2008.0']
 ['17/10000217_1981-05-05_2009.jpg' '48/10000548_1925-04-04_1964.jpg'
  '12/100012_1948-07-03_2008.jpg' ... '09/9998109_1972-12-27_2013.jpg'
  '00/9999400_1981-12-13_2011.jpg' '80/999980_1954-06-11_2008.jpg']
 ...
 ['1.0' '1.0' '1.0' ... '1.0' '1.0' '0.0']
 ['4.3009623883308095' '2.6456394971903463' '4.329328832406529' ...
  '3.4943031690208564' '-inf' '5.486916546849864']
 ['nan' '1.9492479052091165' 'nan' ... 'nan' 'nan' 'nan']]


In [58]:
import pandas as pd

print(data.shape)
df = pd.DataFrame(data).transpose()
df.columns = fields

df

(8, 62328)


dob photo_taken                        full_path gender  \
0      723671.0      2009.0  17/10000217_1981-05-05_2009.jpg    1.0   
1      703186.0      1964.0  48/10000548_1925-04-04_1964.jpg    1.0   
2      711677.0      2008.0    12/100012_1948-07-03_2008.jpg    1.0   
3      705061.0      1961.0  65/10001965_1930-05-23_1961.jpg    1.0   
4      720044.0      2012.0  16/10002116_1971-05-31_2012.jpg    0.0   
...         ...         ...                              ...    ...   
62323  707582.0      1963.0   49/9996949_1937-04-17_1963.jpg    1.0   
62324  711338.0      1970.0   32/9997032_1947-07-30_1970.jpg    1.0   
62325  720620.0      2013.0   09/9998109_1972-12-27_2013.jpg    1.0   
62326  723893.0      2011.0   00/9999400_1981-12-13_2011.jpg    1.0   
62327  713846.0      2008.0    80/999980_1954-06-11_2008.jpg    0.0   

                        name face_location          face_score  \
0            Sami Jauhojärvi           1.0  4.3009623883308095   
1             Dettmar Cramer           1.0  2.6456394971903463   
2                Marc Okrand           1.0   4.329328832406529   
3       Aleksandar Matanović           1.0                -inf   
4               Diana Damrau           0.0   3.408442415222501   
...                      ...           ...                 ...   
62323                    0.0           1.0   4.029267756985114   
62324                    0.0           1.0                -inf   
62325  4.68486041878186e-310           1.0  3.4943031690208564   
62326  4.68486041878186e-310           1.0                -inf   
62327  6.92474272034567e-310           0.0   5.486916546849864   

        second_face_score  
0                     nan  
1      1.9492479052091165  
2                     nan  
3                     nan  
4                     nan  
...                   ...  
62323                 nan  
62324                 nan  
62325                 nan  
62326                 nan  
62327                 nan  

[62328 rows x 8 columns]